In [219]:
import pandas as pd
import numpy as np
from sklearn.preprocessing import OneHotEncoder

In [220]:
data_train = pd.read_csv('train.csv')
data_test = pd.read_csv('test.csv')

# Metadata

 - <i><b>encounter_id</i></b> - Unique identifier of the encounter
 - <i><b>country</i></b> - country
 - <i><b>patient_id</i></b> - Identifier of the patient
 - <i><b>race</i></b> - Patient’s race
 - <i><b>gender</i></b> - Patient’s gender
 - <i><b>age</i></b> - Patient’s age bracket
 - <i><b>weight</i></b> - Patient’s weight
 - <i><b>payer_code</i></b> - Code of the health insurance provider (if there is one)
 - <i><b>outpatient_visits_in_previous_year</i></b> - Number of outpatient visits (visits made with the intention of leaving on the same day) the patient made to the hospital in the year preceding the encounter
 - <i><b>emergency_visits_in_previous_year</i></b> - Number of emergency visits the patient made to the hospital in the year preceding the encounter
 - <i><b>inpatient_visits_in_previous_year</i></b> - Number of inpatient visits (visits with the intention to stay overnight) the patient made to the hospital in the year preceding the encounter
 - <i><b>admission_type</i></b> - Type of admission of the patient (e.g. Emergency, Urgent,etc…)
 - <i><b>medical_specialty</i></b> - Medical specialty on which the patient was admitted
 - <i><b>average_pulse_bpm</i></b> - Average pulse of the patient during their stay in the hospital in beats per minute
 - <i><b>discharge_disposition</i></b> - Destination given to the patient after being discharged
 - <i><b>admission_source</i></b> - Source of the patient before being admitted in the current encounter
 - <i><b>length_of_stay_in_hospital</i></b> - Number of days between admission and discharge
 - <i><b>number_lab_tests</i></b> - Number of lab tests performed during the encounter
 - <i><b>non_lab_procedures</i></b> - Number of non-lab procedures performed during the encounter
 - <i><b>number_of_medications</i></b> - Number of distinct types of medication administered during the encounter
 - <i><b>primary_diagnosis</i></b> - Primary diagnosis (coded as first three digits of ICD9)
 - <i><b>secondary_diagnosis</i></b> - Secondary diagnosis (first three digits of ICD9)
 - <i><b>additional_diagnosis</i></b> - Additional secondary diagnosis (first three digits of ICD9)
 - <i><b>number_diagnoses</i></b> - Number of diagnosis entered to the system
 - <i><b>glucose_test_result</i></b> - Range  of the glucose test results or if the test was not taken. Values: ">200", ">300", "normal", and "none" if not measured
 - <i><b>a1c_test_results</i></b> - Range of the A1C test results or if the test was not taken. Values: ">8" if greater than 8%, ">7" if greater than 7% but less than 8%, "normal" if less than 7% and "none" if not measured
 - <i><b>change_in_meds_during_hospitalization</i></b> - Indicates if there was a change in diabetic medications (dosage or generic name). Values: "change" and "no change"
 - <i><b>perscribed_diabetes_meds</i></b> - Yes if patient has diabetes medication perscription. No otherwise.
 - <i><b>medication</i></b>- List containing all generic names for the medications perscribed to the patient during the encounter. Empty if no medication was perscribed
 - <i><b>readmitted_binary</i></b> - Binary Target: Yes if patient was readmitted in less than 30 days. No otherwise.
 - <i><b>readmitted_multiclass</i></b> - Multiclass Target: "<30 days" if patient was readmitted in less than 30 days after being discharged. ">30 days" if patient was readmitted to the hospital but only after more than 30 days after the current discharged. No otherwise

# Data Preprocessing

In [221]:
# We can see question marks that represent missing values
# So before we actually handle missing values, we will transform all missing values into NaN types
data_train

encounter_id country  patient_id             race  gender      age  \
0            533253     USA       70110        Caucasian  Female  [70-80)   
1            426224     USA    29775006  AfricanAmerican    Male  [50-60)   
2            634063     USA    80729253        Caucasian  Female  [60-70)   
3            890610     USA     2919042  AfricanAmerican    Male  [60-70)   
4            654194     USA    84871971        Caucasian  Female  [70-80)   
...             ...     ...         ...              ...     ...      ...   
71231        660160     USA    24531381  AfricanAmerican  Female  [80-90)   
71232        826429     USA     4663818  AfricanAmerican  Female  [70-80)   
71233        332030     USA    23397147        Caucasian  Female  [60-70)   
71234        757560     USA    52161750        Caucasian    Male  [60-70)   
71235        459757     USA    88410897        Caucasian    Male  [70-80)   

      weight payer_code  outpatient_visits_in_previous_year  \
0          ?          ?                                   0   
1          ?          ?                                   0   
2          ?          ?                                   0   
3          ?         MC                                   0   
4          ?         HM                                   1   
...      ...        ...                                 ...   
71231      ?         MC                                   0   
71232      ?          ?                                   0   
71233      ?          ?                                   0   
71234      ?         BC                                   0   
71235      ?         BC                                   0   

       emergency_visits_in_previous_year  ...  secondary_diagnosis  \
0                                      0  ...                  276   
1                                      0  ...                  785   
2                                      0  ...                  135   
3                                      0  ...                  562   
4                                      0  ...                  599   
...                                  ...  ...                  ...   
71231                                  1  ...                  786   
71232                                  0  ...                  197   
71233                                  2  ...                  491   
71234                                  0  ...                  157   
71235                                  0  ...                  250   

      additional_diagnosis number_diagnoses  glucose_test_result  \
0                      466                8                  NaN   
1                      162                9                  NaN   
2                      250                6                  NaN   
3                      455                5                  NaN   
4                      428                9                  NaN   
...                    ...              ...                  ...   
71231                  250                9                  NaN   
71232                  V66                6                  NaN   
71233                  276                9                 >300   
71234                250.8                5                  NaN   
71235                  401                8                  NaN   

      a1c_test_result change_in_meds_during_hospitalization  \
0                 NaN                                    No   
1                 NaN                                    No   
2                 NaN                                    Ch   
3                 NaN                                    No   
4                 NaN                                    No   
...               ...                                   ...   
71231              >7                                    Ch   
71232              >7                                    Ch   
71233             NaN                                    Ch   
71234             NaN                

In [222]:
data_train.replace('?', np.nan, inplace = True)
data_test.replace('?', np.nan, inplace = True)
data_train

encounter_id country  patient_id             race  gender      age  \
0            533253     USA       70110        Caucasian  Female  [70-80)   
1            426224     USA    29775006  AfricanAmerican    Male  [50-60)   
2            634063     USA    80729253        Caucasian  Female  [60-70)   
3            890610     USA     2919042  AfricanAmerican    Male  [60-70)   
4            654194     USA    84871971        Caucasian  Female  [70-80)   
...             ...     ...         ...              ...     ...      ...   
71231        660160     USA    24531381  AfricanAmerican  Female  [80-90)   
71232        826429     USA     4663818  AfricanAmerican  Female  [70-80)   
71233        332030     USA    23397147        Caucasian  Female  [60-70)   
71234        757560     USA    52161750        Caucasian    Male  [60-70)   
71235        459757     USA    88410897        Caucasian    Male  [70-80)   

      weight payer_code  outpatient_visits_in_previous_year  \
0        NaN        NaN                                   0   
1        NaN        NaN                                   0   
2        NaN        NaN                                   0   
3        NaN         MC                                   0   
4        NaN         HM                                   1   
...      ...        ...                                 ...   
71231    NaN         MC                                   0   
71232    NaN        NaN                                   0   
71233    NaN        NaN                                   0   
71234    NaN         BC                                   0   
71235    NaN         BC                                   0   

       emergency_visits_in_previous_year  ...  secondary_diagnosis  \
0                                      0  ...                  276   
1                                      0  ...                  785   
2                                      0  ...                  135   
3                                      0  ...                  562   
4                                      0  ...                  599   
...                                  ...  ...                  ...   
71231                                  1  ...                  786   
71232                                  0  ...                  197   
71233                                  2  ...                  491   
71234                                  0  ...                  157   
71235                                  0  ...                  250   

      additional_diagnosis number_diagnoses  glucose_test_result  \
0                      466                8                  NaN   
1                      162                9                  NaN   
2                      250                6                  NaN   
3                      455                5                  NaN   
4                      428                9                  NaN   
...                    ...              ...                  ...   
71231                  250                9                  NaN   
71232                  V66                6                  NaN   
71233                  276                9                 >300   
71234                250.8                5                  NaN   
71235                  401                8                  NaN   

      a1c_test_result change_in_meds_during_hospitalization  \
0                 NaN                                    No   
1                 NaN                                    No   
2                 NaN                                    Ch   
3                 NaN                                    No   
4                 NaN                                    No   
...               ...                                   ...   
71231              >7                                    Ch   
71232              >7                                    Ch   
71233             NaN                                    Ch   
71234             NaN                

In [223]:
# Now we can see how many missing values we have for each feature
data_train.isna().sum()

encounter_id                                 0
country                                      0
patient_id                                   0
race                                      5070
gender                                       0
age                                       3557
weight                                   68990
payer_code                               28201
outpatient_visits_in_previous_year           0
emergency_visits_in_previous_year            0
inpatient_visits_in_previous_year            0
admission_type                            3706
medical_specialty                        34922
average_pulse_bpm                            0
discharge_disposition                     2590
admission_source                          4718
length_of_stay_in_hospital                   0
number_lab_tests                             0
non_lab_procedures                           0
number_of_medications                        0
primary_diagnosis                           16
secondary_dia

In [224]:
# Transforming target variable into binary
data_train['readmitted_binary'] = data_train['readmitted_binary'].replace({'Yes': 1, 'No': 0}).astype(int)

# We can already check that our data is unbalanced
data_train['readmitted_binary'].value_counts()

0    63286
1     7950
Name: readmitted_binary, dtype: int64

In [225]:
# The country has no missing values and only one value so it is an irrelevant variable
data_train['country'].value_counts()

data_train.drop(columns = 'country', inplace = True)
data_test.drop(columns = 'country', inplace = True)

data_train

encounter_id  patient_id             race  gender      age weight  \
0            533253       70110        Caucasian  Female  [70-80)    NaN   
1            426224    29775006  AfricanAmerican    Male  [50-60)    NaN   
2            634063    80729253        Caucasian  Female  [60-70)    NaN   
3            890610     2919042  AfricanAmerican    Male  [60-70)    NaN   
4            654194    84871971        Caucasian  Female  [70-80)    NaN   
...             ...         ...              ...     ...      ...    ...   
71231        660160    24531381  AfricanAmerican  Female  [80-90)    NaN   
71232        826429     4663818  AfricanAmerican  Female  [70-80)    NaN   
71233        332030    23397147        Caucasian  Female  [60-70)    NaN   
71234        757560    52161750        Caucasian    Male  [60-70)    NaN   
71235        459757    88410897        Caucasian    Male  [70-80)    NaN   

      payer_code  outpatient_visits_in_previous_year  \
0            NaN                                   0   
1            NaN                                   0   
2            NaN                                   0   
3             MC                                   0   
4             HM                                   1   
...          ...                                 ...   
71231         MC                                   0   
71232        NaN                                   0   
71233        NaN                                   0   
71234         BC                                   0   
71235         BC                                   0   

       emergency_visits_in_previous_year  inpatient_visits_in_previous_year  \
0                                      0                                  2   
1                                      0                                  0   
2                                      0                                  1   
3                                      0                                  1   
4                                      0                                  0   
...                                  ...                                ...   
71231                                  1                                  0   
71232                                  0                                  0   
71233                                  2                                  2   
71234                                  0                                  2   
71235                                  0                                  1   

       ... secondary_diagnosis additional_diagnosis  number_diagnoses  \
0      ...                 276                  466                 8   
1      ...                 785                  162                 9   
2      ...                 135                  250                 6   
3      ...                 562                  455                 5   
4      ...                 599                  428                 9   
...    ...                 ...                  ...               ...   
71231  ...                 786                  250                 9   
71232  ...                 197                  V66                 6   
71233  ...                 491                  276                 9   
71234  ...                 157                250.8                 5   
71235  ...                 250                  401                 8   

      glucose_test_result a1c_test_result  \
0                     NaN             NaN   
1                     NaN             NaN   
2                     NaN             NaN   
3                     NaN             NaN   
4                     NaN             NaN   
...                   ...             ...   
71231                 NaN              >7   
71232                 NaN              >7   
71233                >300             NaN   
71234                 NaN             NaN   
71235                 NaN             NaN   

       change_in_meds_during_hospitalization  prescrib

In [226]:
# Using One Hot Enconder for the race variable
encoder = OneHotEncoder(sparse_output = False)

encoder_race_train = encoder.fit_transform(data_train['race'].values.reshape(-1, 1))
encoder_race_test = encoder.transform(data_test['race'].values.reshape(-1, 1))

data_train = pd.concat([data_train, pd.DataFrame(encoder_race_train, columns=encoder.get_feature_names_out(['race']))], axis=1)
data_test = pd.concat([data_test, pd.DataFrame(encoder_race_test, columns = encoder.get_feature_names_out(['race']))], axis = 1)

data_train.drop(columns = 'race', inplace = True)
data_test.drop(columns = 'race', inplace = True)

data_train.columns

Index(['encounter_id', 'patient_id', 'gender', 'age', 'weight', 'payer_code',
       'outpatient_visits_in_previous_year',
       'emergency_visits_in_previous_year',
       'inpatient_visits_in_previous_year', 'admission_type',
       'medical_specialty', 'average_pulse_bpm', 'discharge_disposition',
       'admission_source', 'length_of_stay_in_hospital', 'number_lab_tests',
       'non_lab_procedures', 'number_of_medications', 'primary_diagnosis',
       'secondary_diagnosis', 'additional_diagnosis', 'number_diagnoses',
       'glucose_test_result', 'a1c_test_result',
       'change_in_meds_during_hospitalization', 'prescribed_diabetes_meds',
       'medication', 'readmitted_binary', 'readmitted_multiclass',
       'race_AfricanAmerican', 'race_Asian', 'race_Caucasian', 'race_Hispanic',
       'race_Other', 'race_nan'],
      dtype='object')

In [227]:
# Check all gender values
data_train['gender'].unique()

array(['Female', 'Male', 'Unknown/Invalid'], dtype=object)

In [228]:
# Transforming gender into a categorical variable
data_train['gender'] = data_train['gender'].replace({'Female': 1, 'Male': 0, 'Unknown/Invalid': np.nan}).astype(float)
data_test['gender'] = data_test['gender'].replace({'Female': 1, 'Male': 0, 'Unknown/Invalid': np.nan}).astype(float)

data_train['gender'].value_counts()

1.0    38228
0.0    33005
Name: gender, dtype: int64

In [229]:
data_train['gender'].isna().sum()

3

In [230]:
# These are the only 3 patients with the gender information missing
# After searching for patient id, we conclude it is the first time these patients come to the hospital
# So we can't replace these missing values with the information from previous visits
data_train[pd.isna(data_train['gender'])]

encounter_id  patient_id  gender      age weight payer_code  \
7057         208080    78119847     NaN  [70-80)    NaN         CP   
43834        978787    60524946     NaN  [60-70)    NaN         CP   
64443        876217   100695042     NaN  [70-80)    NaN        NaN   

       outpatient_visits_in_previous_year  emergency_visits_in_previous_year  \
7057                                    0                                  0   
43834                                   0                                  0   
64443                                   0                                  0   

       inpatient_visits_in_previous_year admission_type  ...  \
7057                                   0      Emergency  ...   
43834                                  0      Emergency  ...   
64443                                  0       Elective  ...   

      prescribed_diabetes_meds                      medication  \
7057                       Yes  ['metformin', 'rosiglitazone']   
43834                       No                              []   
64443                      Yes   ['glipizide', 'pioglitazone']   

      readmitted_binary readmitted_multiclass  race_AfricanAmerican  \
7057                  0                    No                   0.0   
43834                 0                    No                   0.0   
64443                 0                    No                   0.0   

       race_Asian  race_Caucasian  race_Hispanic race_Other race_nan  
7057          0.0             0.0            0.0        0.0      1.0  
43834         0.0             0.0            0.0        0.0      1.0  
64443         0.0             0.0            0.0        1.0      0.0  

[3 rows x 35 columns]

In [231]:
#encoding age as label encoding with bigger number if the age is bigger
data_train['age'] = data_train['age'].replace({'[0-10)': 5,
                                           '[10-20)': 15,
                                           '[20-30)': 25,
                                           '[30-40)': 35,
                                           '[40-50)': 45,
                                           '[50-60)': 55,
                                           '[60-70)': 65,
                                           '[70-80)': 75,
                                           '[80-90)': 85,
                                           '[90-100)': 95})

data_test['age'] = data_test['age'].replace({'[0-10)': 5,
                                           '[10-20)': 15,
                                           '[20-30)': 25,
                                           '[30-40)': 35,
                                           '[40-50)': 45,
                                           '[50-60)': 55,
                                           '[60-70)': 65,
                                           '[70-80)': 75,
                                           '[80-90)': 85,
                                           '[90-100)': 95})

data_train

encounter_id  patient_id  gender   age weight payer_code  \
0            533253       70110     1.0  75.0    NaN        NaN   
1            426224    29775006     0.0  55.0    NaN        NaN   
2            634063    80729253     1.0  65.0    NaN        NaN   
3            890610     2919042     0.0  65.0    NaN         MC   
4            654194    84871971     1.0  75.0    NaN         HM   
...             ...         ...     ...   ...    ...        ...   
71231        660160    24531381     1.0  85.0    NaN         MC   
71232        826429     4663818     1.0  75.0    NaN        NaN   
71233        332030    23397147     1.0  65.0    NaN        NaN   
71234        757560    52161750     0.0  65.0    NaN         BC   
71235        459757    88410897     0.0  75.0    NaN         BC   

       outpatient_visits_in_previous_year  emergency_visits_in_previous_year  \
0                                       0                                  0   
1                                       0                                  0   
2                                       0                                  0   
3                                       0                                  0   
4                                       1                                  0   
...                                   ...                                ...   
71231                                   0                                  1   
71232                                   0                                  0   
71233                                   0                                  2   
71234                                   0                                  0   
71235                                   0                                  0   

       inpatient_visits_in_previous_year admission_type  ...  \
0                                      2      Emergency  ...   
1                                      0      Emergency  ...   
2                                      1            NaN  ...   
3                                      1      Emergency  ...   
4                                      0       Elective  ...   
...                                  ...            ...  ...   
71231                                  0       Elective  ...   
71232                                  0         Urgent  ...   
71233                                  2            NaN  ...   
71234                                  2      Emergency  ...   
71235                                  1         Urgent  ...   

      prescribed_diabetes_meds                             medication  \
0                           No                                     []   
1                          Yes                            ['insulin']   
2                          Yes             ['glimepiride', 'insulin']   
3                           No                                     []   
4                           No                                     []   
...                        ...                                    ...   
71231                      Yes  ['metformin', 'glyburide', 'insulin']   
71232                      Yes             ['metformin', 'glyburide']   
71233                      Yes               ['glyburide', 'insulin']   
71234                      Yes               ['glyburide', 'insulin']   
71235                      Yes                            ['insulin']   

      readmitted_binary readmitted_multiclass  race_AfricanAmerican  \
0                     0              >30 days                   0.0   
1                     0                    No                   1.0   
2                     0                    No                   0.0   
3                     0                    No                   1.0   
4                     0              >30 days                   0.0   
...                 ...                   ...                   ...   
71231                 0                    No                   1.0   
71232                 0    

In [232]:
data_train['age'].isna().sum()

3557

In [233]:
patients_age_missing = data_train[pd.isna(data_train['age'])]['patient_id']

In [234]:
data_sorted = data_train.sort_values(['patient_id', 'encounter_id'])
data_sorted['age'] = data_sorted.groupby('patient_id')['age'].fillna(method = 'ffill')

In [235]:
data_sorted['age'] = data_sorted.groupby('patient_id')['age'].fillna(method='bfill')

In [236]:
for patient in patients_age_missing:
    print(data_sorted[data_sorted['patient_id'] == patient])

       encounter_id  patient_id  gender   age weight payer_code  \
67152        580952    24854895     0.0  55.0    NaN        NaN   
19           844139    24854895     0.0  55.0    NaN        NaN   
7297         844615    24854895     0.0  55.0    NaN        NaN   

       outpatient_visits_in_previous_year  emergency_visits_in_previous_year  \
67152                                   0                                  0   
19                                      0                                  0   
7297                                    0                                  0   

       inpatient_visits_in_previous_year admission_type  ...  \
67152                                  0  Not Available  ...   
19                                     1  Not Available  ...   
7297                                   2  Not Available  ...   

      prescribed_diabetes_meds                                medication  \
67152                      Yes  ['metformin', 'pioglitazone', 'insulin']   
1

     encounter_id  patient_id  gender  age weight payer_code  \
981        394676    69440796     0.0  NaN    NaN        NaN   

     outpatient_visits_in_previous_year  emergency_visits_in_previous_year  \
981                                   0                                  0   

     inpatient_visits_in_previous_year admission_type  ...  \
981                                  0      Emergency  ...   

    prescribed_diabetes_meds  medication readmitted_binary  \
981                       No          []                 0   

    readmitted_multiclass  race_AfricanAmerican  race_Asian  race_Caucasian  \
981              >30 days                   0.0         0.0             1.0   

     race_Hispanic race_Other race_nan  
981            0.0        0.0      0.0  

[1 rows x 35 columns]
     encounter_id  patient_id  gender  age weight payer_code  \
986        911548    70876575     1.0  NaN    NaN         MC   

     outpatient_visits_in_previous_year  emergency_visits_in_previous_y

       encounter_id  patient_id  gender   age weight payer_code  \
65160        137968    49203315     0.0  45.0    NaN        NaN   
29713        151493    49203315     0.0  45.0    NaN        NaN   
17207        667588    49203315     0.0  45.0    NaN        NaN   
1855         669355    49203315     0.0  45.0    NaN        NaN   

       outpatient_visits_in_previous_year  emergency_visits_in_previous_year  \
65160                                   0                                  0   
29713                                   0                                  0   
17207                                   0                                  0   
1855                                    0                                  0   

       inpatient_visits_in_previous_year admission_type  ...  \
65160                                  0         Urgent  ...   
29713                                  4         Urgent  ...   
17207                                  1         Urgent  ...   
1855   

      encounter_id  patient_id  gender  age weight payer_code  \
2746        893216    96363351     1.0  NaN    NaN        NaN   

      outpatient_visits_in_previous_year  emergency_visits_in_previous_year  \
2746                                   2                                  0   

      inpatient_visits_in_previous_year admission_type  ...  \
2746                                  0      Emergency  ...   

     prescribed_diabetes_meds                                medication  \
2746                      Yes  ['metformin', 'pioglitazone', 'insulin']   

     readmitted_binary readmitted_multiclass  race_AfricanAmerican  \
2746                 0                    No                   0.0   

      race_Asian  race_Caucasian  race_Hispanic race_Other race_nan  
2746         0.0             1.0            0.0        0.0      0.0  

[1 rows x 35 columns]
      encounter_id  patient_id  gender  age weight payer_code  \
2748        417793    90429210     0.0  NaN    NaN         MC  

      encounter_id  patient_id  gender  age weight payer_code  \
3585        188025    70910982     0.0  NaN    NaN         CP   

      outpatient_visits_in_previous_year  emergency_visits_in_previous_year  \
3585                                   0                                  0   

      inpatient_visits_in_previous_year admission_type  ...  \
3585                                  1       Elective  ...   

     prescribed_diabetes_meds                             medication  \
3585                      Yes  ['metformin', 'glipizide', 'insulin']   

     readmitted_binary readmitted_multiclass  race_AfricanAmerican  \
3585                 0                    No                   0.0   

      race_Asian  race_Caucasian  race_Hispanic race_Other race_nan  
3585         0.0             1.0            0.0        0.0      0.0  

[1 rows x 35 columns]
       encounter_id  patient_id  gender   age weight payer_code  \
3594         421342    87442686     1.0  85.0    NaN         MC   


...

       encounter_id  patient_id  gender   age weight payer_code  \
1788         340848    14189319     0.0  45.0    NaN        NaN   
66027        603356    14189319     0.0  45.0    NaN        NaN   
68491        864125    14189319     0.0  45.0    NaN        NaN   

       outpatient_visits_in_previous_year  emergency_visits_in_previous_year  \
1788                                    0                                  0   
66027                                   1                                  0   
68491                                   0                                  0   

       inpatient_visits_in_previous_year admission_type  ...  \
1788                                   1      Emergency  ...   
66027                                  2         Urgent  ...   
68491                                  0       Elective  ...   

      prescribed_diabetes_meds   medication readmitted_binary  \
1788                       Yes  ['insulin']                 1   
66027                  

       encounter_id  patient_id  gender  age weight payer_code  \
67159        173665    95924124     0.0  NaN    NaN         MC   

       outpatient_visits_in_previous_year  emergency_visits_in_previous_year  \
67159                                   0                                  0   

       inpatient_visits_in_previous_year admission_type  ...  \
67159                                  1  Not Available  ...   

      prescribed_diabetes_meds   medication readmitted_binary  \
67159                      Yes  ['insulin']                 0   

      readmitted_multiclass  race_AfricanAmerican  race_Asian  race_Caucasian  \
67159                    No                   1.0         0.0             0.0   

       race_Hispanic race_Other race_nan  
67159            0.0        0.0      0.0  

[1 rows x 35 columns]
       encounter_id  patient_id  gender   age weight payer_code  \
67190        181301    86176467     1.0  85.0    NaN         MC   
1733         261616    86176467     1.0 

       encounter_id  patient_id  gender  age weight payer_code  \
68224        582747    20339145     0.0  NaN    NaN        NaN   

       outpatient_visits_in_previous_year  emergency_visits_in_previous_year  \
68224                                   0                                  0   

       inpatient_visits_in_previous_year admission_type  ...  \
68224                                  0       Elective  ...   

      prescribed_diabetes_meds     medication readmitted_binary  \
68224                      Yes  ['glipizide']                 0   

      readmitted_multiclass  race_AfricanAmerican  race_Asian  race_Caucasian  \
68224                    No                   0.0         0.0             1.0   

       race_Hispanic race_Other race_nan  
68224            0.0        0.0      0.0  

[1 rows x 35 columns]
       encounter_id  patient_id  gender  age     weight payer_code  \
68259        896989    71688843     1.0  NaN  [100-125)         CP   

       outpatient_visits_in_p

       encounter_id  patient_id  gender  age weight payer_code  \
69440        401073    88257078     0.0  NaN    NaN         MC   

       outpatient_visits_in_previous_year  emergency_visits_in_previous_year  \
69440                                   0                                  0   

       inpatient_visits_in_previous_year admission_type  ...  \
69440                                  0  Not Available  ...   

      prescribed_diabetes_meds                medication readmitted_binary  \
69440                      Yes  ['glyburide', 'insulin']                 0   

      readmitted_multiclass  race_AfricanAmerican  race_Asian  race_Caucasian  \
69440                    No                   0.0         0.0             1.0   

       race_Hispanic race_Other race_nan  
69440            0.0        0.0      0.0  

[1 rows x 35 columns]
       encounter_id  patient_id  gender  age weight payer_code  \
69444        160547   108298413     0.0  NaN    NaN         MC   

       outpatie

       encounter_id  patient_id  gender  age weight payer_code  \
70647        506998    34491087     0.0  NaN    NaN         MD   

       outpatient_visits_in_previous_year  emergency_visits_in_previous_year  \
70647                                   0                                  0   

       inpatient_visits_in_previous_year admission_type  ...  \
70647                                  1       Elective  ...   

      prescribed_diabetes_meds       medication readmitted_binary  \
70647                      Yes  ['glimepiride']                 0   

      readmitted_multiclass  race_AfricanAmerican  race_Asian  race_Caucasian  \
70647                    No                   0.0         0.0             1.0   

       race_Hispanic race_Other race_nan  
70647            0.0        0.0      0.0  

[1 rows x 35 columns]
       encounter_id  patient_id  gender  age weight payer_code  \
70706        427184    79403184     0.0  NaN    NaN         MC   

       outpatient_visits_in_previ

In [237]:
data_sorted['age'].isna().sum()

2217